# Sujet 1 - Concentration de CO2 dans l'atmosphère depuis 1958

In [ ]:
%matplotlib inline
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd

## Récupération des données et analyse préliminaire

Les données sur la concentration de CO2 dans l'atmosphère à l'observatoire de Mauna Loa sont disponibles sur le site web de l'[institut Scripps](https://scrippsco2.ucsd.edu/data/atmospheric_co2/primary_mlo_co2_record.html). La série de données s'étend de 1958 à nos jours. Les données considérées sont les relevés avec une granularité hebdomadaire. Elles sont disponibles à l'adresse suivante:

In [ ]:
data_url = "https://scrippsco2.ucsd.edu/assets/data/atmospheric/stations/in_situ_co2/weekly/weekly_in_situ_co2_mlo.csv"

Pour nous protéger contre une éventuelle disparition ou modification du serveur de l'institut Scripps, nous faisons une copie locale de ce jeux de données que nous préservons avec notre analyse. Il est inutile et même risquée de télécharger les données à chaque exécution, car dans le cas d'une panne nous pourrions remplacer nos données par un fichier défectueux. Pour cette raison, nous téléchargeons les données seulement si la copie locale n'existe pas.

In [ ]:
data_file = "CO2_Mauna_Loa_Hebdo.csv"

In [ ]:
import os
import urllib.request
if not os.path.exists(data_file):
    urllib.request.urlretrieve(data_url, data_file)

Le jeu de données est téléchargé le 01/10/2020 à 17h44.

Un examen préliminaire des données permet d'en observer la structure.

On note que les 44 premières lignes décrivent le contexte général. Ellent devront donc être supprimées lors de l'extraction des données.

Les lignes 40 à 44 précisent que les unités de concentration de CO2 sont des micro-moles de CO2 par mole (ppm). Ces valeurs sont considérées à 12h00 le samedi de chaque semaine.

On note également que les dates sont au format "AAAA-MM-JJ".

In [ ]:
Lignes = []
with open(data_file, "r", encoding='utf-8') as entree:
    for ligne in entree:
        Lignes.append(ligne)
for Cpt in range(60):
    print(Cpt+1, Lignes[Cpt])

On charge les données à partir de la ligne 45 et on examine leur teneur.

In [ ]:
raw_data = pd.read_csv(data_file, skiprows=44, names=['Date', 'CO2'], parse_dates=[0], infer_datetime_format=True)
raw_data.head()

In [ ]:
raw_data.tail()

In [ ]:
date_début = raw_data.loc[raw_data.index.start, 'Date']
date_fin = raw_data.loc[raw_data.index.stop-1, 'Date']
print(f"On remarque que les données couvrent la période allant du {date_début.strftime('%d/%m/%Y')} au {date_fin.strftime('%d/%m/%Y')}.")

Nous pouvons vérifier si des données sont manquantes. Il semble que non (pas de valeur nulle).

In [ ]:
raw_data[raw_data.isnull().any(axis=1)]

Manque-t-il des données (des semaines non enregistrées)? Pour cela, nous allons vérifier que l'écart entre deux dates consécutives est bien de 7 jours.

On note que de nombreuses dates sont manquantes. Dans certains cas, ce sont plusieurs semaines qui sont manquantes.

In [ ]:
# Calculer les écarts de dates entre deux index contigüs. Si l'écart n'est pas égal à 7 jours, afficher les deux lignes.
for cpt in range (raw_data.index.start, raw_data.index.stop-1):
    début = raw_data.loc[raw_data.index.start:raw_data.index.stop, 'Date'][cpt]
    fin = raw_data.loc[raw_data.index.start:raw_data.index.stop, 'Date'][cpt+1]
    if str(fin-début) != '7 days 00:00:00':
        print(cpt, ':', début, ' - ', cpt+1, ':', fin, ' - ', fin-début)

Si nous tentons d'analyser les données et surtout de modéliser leur tendance en les approchant par un polynôme, nous allons obtenir des résultats erronés. En effet, la variable d'entrée du polynôme pour obtenir une évaluation sera la colonne des indice des lignes du tableau. Comme les dates et les indices n'évoluent pas de manière conjointe, les résultats des prévisions en seront affectés.

On se propose donc de créer un data frame avec toutes les semaines depuis le début des mesures, le 29/03/1958, jusqu'à la fin de l'année 2025. Les données déjà disponibles seront alors jointées dans ce data frame. Les nouvelles prévisions seront également ajoutées. Le modèle de prévision de la tendance de long terme pourra alors être ajusté.

## Recontruction d'un jeu de données complété

Création d'un data frame avec toutes les dates depuis le 29/03/1958 jusqu'à la fin de l'année 2025.

In [ ]:
tab_date = pd.date_range(start='1958-03-29', end='2026-01-01', periods=None, freq='7D', normalize=False, name=None)
df = pd.DataFrame(tab_date, columns=['Date'])

Pour chaque date, le numéro de la semaine est calculé. Cette colonne est ajoutée au data frame.

In [ ]:
tab_week = []
df_début = df.index.start
df_fin = df.index.stop

for cpt in range(df_début, df_fin):
    date = df.loc[df.index.start:df.index.stop, 'Date'][cpt]
    tab_week.append(pd.Period(date, 'D').week)

df = df.assign(Week = tab_week)

Nous allons intégrer les mesures dans ce data frame.

In [ ]:
df = df.merge(raw_data, on='Date', how='outer')
df[4:16]

## Observation du rendu des données disponibles

Nous pouvons afficher les données. Nous observons une tendance globale de hausse et un phénomène qui semble périodique ou saisonnier.

In [ ]:
df.plot('Date', 'CO2')

Un graphique sur une période plus réduite permet de mieux observer le phénomène saisonnier.

Il semble que le point bas du phénomène saisonnier se situe vers le mois d'octobre et son haut vers le mois de mai.

In [ ]:
df[-500:-300].plot('Date', 'CO2')

On observe l'absence de données sur certaines périodes.

In [ ]:
df[200:350].plot('Date', 'CO2')

## Elaboration d'un modèle prévisionnel de la tendance de long terme

Nous nous proposons de tenter d'approcher cette courbe par un polynôme du second degré. L'ajustement du polynôme sera réalisé en minimisant la somme du carré des écarts. Cela devrait placer la courbe résultante comme la position moyenne du phénomène. On note un écart significatif entre la dynamique de la tendance de long terme et celle du phénomène saisonnier. Les deux parties du phénomène devraient donc pouvoir être correctement séparées. La tendance de long terme devrait pouvoir être approchée par un polynôme du second degré.

Toutefois, le data frame contient de nombreuses données manquantes ('NaN'). La présence de ces données manquantes pose problème à l'algorithme d'ajustement du polynôme. Il faut donc limiter l'ajustement à la période de mesure disponible (indice 0 à 3255, cf. ci-dessous). Pour les données manquantes à l'intérieur de cette période, nous utiliserons une interpolation linéaire qui ne devrait trop affecter le résultat final.

In [ ]:
df[3250:3260]

On observe que les données manquantes à l'intérieur de la période de mesure sont maintenant renseignées.

In [ ]:
df_lt = df[0:3256]
df_lt = df_lt.interpolate()

In [ ]:
df_lt[4:16]

Nous nous proposons de tenter d'approcher cette courbe par un polynôme du second degré.

In [ ]:
p = np.polyfit(df_lt.index, df_lt['CO2'], deg=2, full=False)
p

Avec ces éléments, nous définissons une fonction qui pour un index donné, retourne une valeur de concentration en CO2 pour la tendance de long terme.

In [ ]:
def taux_lt(x):
    return np.polyval(p, x)

Nous calculons maintenant le taux prévisionnel de long terme pour l'ensemble des index du data frame. Enfin, nous associons ces données au data frame "df".

In [ ]:
prév_lt = []
for cpt in range(df_début, df_fin):
    prév_lt.append(taux_lt(cpt))

df = df.assign(Prév_LT = prév_lt)

In [ ]:
df.head()

In [ ]:
df.tail()

Nous pouvons tracer quelques graphiques pour observer la tendance de long terme qui a été évaluée. La tendance évaluée semble correctement coller au phénomène.

In [ ]:
df.plot('Date', ['CO2', 'Prév_LT'])

In [ ]:
df[-500:-300].plot('Date', ['CO2', 'Prév_LT'])

## Observation du phénomène saisonnier

Pour séparer le phénomène saisonnier de la tendance de long terme, nous calculons la différence entre les mesures de CO2 et la tendance de long terme précédemment évaluée.

In [ ]:
df = df.assign(Saisonnier = df['CO2'] - df['Prév_LT'])
df.head()

Quelques graphiques pour observer le phénomène saisonnier. Le calcul de la moyenne sur la partie saisonnière devrait être proche de 0, si tout va bien. Ce qui semble être le cas.

On notera toutefois une sorte de pseudo période avec ce qui semble être des pics vers 1960, 1990 et 2020.

In [ ]:
df['Saisonnier'].mean()

In [ ]:
df.plot('Date', ['Saisonnier'])

In [ ]:
df[-500:-300].plot('Date', ['Saisonnier'])

## Evaluation du phénomène saisonnier moyen depuis 1958

Nous avons observé que le phénomène saisonnier atteint un pic minimum vers le premier octobre et un point haut vers le mois de mai. Nous avons également observé que de nombreuses semaines de relevés sont manquantes.

Une manière d'aborder le phénomène sans trop se préoccuper ni de son phasage dans l'année ni des données manquantes, serait de calculer la valeur moyenne de la partie saisonnière en fonction de la position de la semaine dans l'année. Cela permettrait d'utiliser au mieux les données disponibles. Une moyenne sur de nombreuses annèes de devrait pas être sensiblement affecter par l'absence de quelques données.

Cela permettrait de raffiner les prévisions ultérieures.

Pour cela, on construit un tableau qui va permettre, pour chaque numéro de semaine de l'année, de cumuler la part saisonnière du taux de CO2 ainsi que le nombre de valeurs considérées. Il suffira ensuite de calculer la valeur moyenne observée pour chacune des semaines.

In [ ]:
# Parcourir le tableau.
# Pour chaque date, calculer la position de la semaine dans l'année.
# Ajouter la valeur du CO2_Saisonnier dans le tableau de résultats et incrémenter le nombre de valeurs
#     disponibles pour ce numéro de semaine.

année = [] # Créer le tableau de résultats.
for i in range (0, 55):
    # La première information est le numéro de semaine,
    #  le second, le cumul de taux, le troisième le nombre de valeurs cumulées.
    # Le quatrième contient la moyenne calculée.
    année.append([i, 0.0, 0, 0.0])
    
for cpt in range(df.index.min(), df.index.max()):
    # Récupérer les informations.
    sem = df.at[cpt, 'Week']
    taux_w = df.at[cpt, 'Saisonnier']
    if pd.isna(taux_w):
        pass
    else:
        année[sem][1] = année[sem][1] +  df.at[cpt, 'Saisonnier']
        année[sem][2] = année[sem][2] + 1

for i in range (0, 55): # Calculer la moyenne pour chaque semaine.
    if année[i][2] != 0:
        année[i][3] = année[i][1] / année[i][2]    

On affiche le tableau résultant afin de vérifier que toutes les semaines ont été correctement traitées et que le nombre des données est suffisant pour que la moyenne ait un sens (de même que l'approche proposée).

In [ ]:
sem = pd.DataFrame(année[1:54], columns=['Num_semaine', 'Cumul', 'Nbre_valeurs', 'Moyenne_semaine'])
sem

Nous pouvons donc éventuellement envisager de compléter les données manquantes dans les mesures en utilisant ce tableau.

On peut afficher la courbe résultante sur le cycle annuel.

In [ ]:
sem.plot('Num_semaine', 'Moyenne_semaine')

## Elaboration d'un modèle prévisionnel du cycle annuel

Nous allons tenter d'approcher le cycle annuel moyen par un polynôme de degré 7. Le résultat semble correct après quelques essais effectués avec des polynômes de degré inférieur.

In [ ]:
p = np.polyfit(sem['Num_semaine'], sem['Moyenne_semaine'], deg=7, full=False)

In [ ]:
def taux_semaine(x):
    return np.polyval(p, x)

Calculer une année de prévision saisonnière.

In [ ]:
prév_sem = []
for cpt in range(sem.index.start+1, sem.index.stop+1):
    prév_sem.append(taux_semaine(cpt))

Afficher le plot. Le phénomène saisonnier moyen est affiché avec le modèle de prévision proposé. Le résultat semble correct.

In [ ]:
sem = sem.assign(Prév_Sem = prév_sem)
sem.plot('Num_semaine', ['Moyenne_semaine', 'Prév_Sem'])

Nous disposons donc d'un modèle de prévision du phénomène saisonnier.

## Comparaison entre les mesures et les prévisions du modèle

Nous calculons pour chaque date du data frame "df", la part saisonnière du taux de CO2 en fonction du numéro de semaine, en utilisant le data frame "sem". Puis nous ajoutons la colonne correspondante au data frame "df".

In [ ]:
prév_sem = []
for cpt in range(df.index.min(), df.index.max()+1):
    w = df.at[cpt, 'Week']
    prév_sem.append(sem.at[w-1, 'Moyenne_semaine'])
df = df.assign(Prév_Sem = prév_sem)

Nous pouvons maintenant calculer la somme des contributions saisonnière et long terme et ajouter la colonne correspondante au data frame "df".

In [ ]:
df = df.assign(Prév_total = df['Prév_LT'] + df['Prév_Sem'])

Nous pouvons maintenant afficher quelques graphiques pour comparer un peu les données mesurées avec les données issues de la prévision.

In [ ]:
df.plot('Date', ['CO2', 'Prév_total'])

In [ ]:
df[-500:-300].plot('Date', ['CO2', 'Prév_total'])

Nous calculons l'écart entre les mesures et les prévisions lorsque cela a un sens (hors valeurs 'NaN').

In [ ]:
Tab_écart_prév = []
for cpt in range(df.index.min(), df.index.max()):
    # Récupérer les informations.
    Ecart_prév = df.at[cpt, 'CO2'] - df.at[cpt, 'Prév_total']
    if pd.isna(Ecart_prév):
        pass
    else:
        Tab_écart_prév.append(Ecart_prév)
df_écart_prév = pd.DataFrame(Tab_écart_prév)

Nous affichons un histogramme afin d'évaluer l'ampleur des erreurs. L'hitogramme ne semble pas être tout à fait une gaussienne. On note cependant que la majorité des erreurs sont proches de 0. La gamme des écarts de prévision vont de -3ppm à +2ppm environ. Les erreurs les plus importantes sont en faible nombre. Pour une valeur de taux de CO2 qui est autour de 300ppm au moins, ces erreurs ne représentent que 1% environ.

In [ ]:
df_écart_prév.hist()

## Prévisions pour l'année 2025

Nous pouvons maintenant établir notre prévision pour l'année 2025. Commençons par afficher le graphique correspondant.

In [ ]:
df[-52:].plot('Date', ['Prév_LT', 'Prév_total'])

On observe un taux moyen annuel (lié à la tendance long terme, choisie au début du mois de juillet), de l'ordre de 425.5ppm. Avec un minimum annuel de 421ppm et un maximum de l'ordre de 428ppm.

Recherchons les valeurs numériques plus précisément.

In [ ]:
moy2025 = round(df[-52:]['Prév_total'].mean(), 2)
min2025 = round(df[-52:]['Prév_total'].min(), 2)
max2025 = round(df[-52:]['Prév_total'].max(), 2)
print(f"Le taux moyen de CO2 prévu pour l'année 2025 est de {moy2025}ppm, avec un minimum de {min2025}ppm et un maximum de {max2025}ppm." )